In [ ]:
#Verificar calidad de dataset

In [7]:
import polars as pl
from typing import Optional, Union, Iterable

In [8]:
ContratosE=pl.scan_csv("data/aprobados/SECOP_II_-_Contratos_Electrónicos_20251120.csv",ignore_errors=True).head(500)
Adiciones=pl.scan_csv("data/aprobados/SECOP_II_-_Adiciones_20251120.csv",ignore_errors=True).head(500)
Ejecucion=pl.scan_csv("data/aprobados/SECOP_II_-_Ejecución_Contratos_20251120.csv",ignore_errors=True).head(500)
#Facturas=pl.scan_csv("data/aprobados/SECOP_II_-_Facturas_20251120.csv",ignore_errors=True).head(500)
#Garantias=pl.scan_csv("data/aprobados/SECOP_II_-_Garantias_20251120.csv",ignore_errors=True).head(500)

In [9]:
pl.Config.set_fmt_float("full")
pl.Config.set_tbl_cols(-1)
def mostrar_informacion(df):
    print("Columnas:")
    print(df.columns)
    print("\nTipos de datos:")
    print(df.dtypes)
    print("\nPrimeras filas:")
    print(df.head(3))
    print("\nEstadísticas descriptivas:")
    print(df.describe())
    print("\nValores nulos por columna:")
    print(df.null_count())
def listas_a_diccionario(claves: list, valores: list) -> dict:
    """
    Construye un diccionario a partir de dos listas del mismo tamaño,
    usando elementos en la misma posición como clave:valor.
    Lanza ValueError si las listas tienen distinto tamaño.
    """
    if len(claves) != len(valores):
        raise ValueError("Las listas deben tener el mismo tamaño")
    return dict(zip(claves, valores))
def clean_col_integer(df, col_name):
    try:
        return df.with_columns(
            pl.col(col_name)
            .str.replace_all(r"[^0-9]", "")
            .cast(pl.Int64, strict=False)
        )
    except :
        return df

def clean_col_date(df, col_name, date_format="%d/%m/%Y"):
    return df.with_columns(
        pl.col(col_name)
        .str.replace_all(r"[^0-9/]", "")
        .str.strptime(pl.Date,format=date_format, strict=False)
    )   

def clean_col_date(df, col_name, date_formats=None):
    """
    Intenta parsear una columna usando varios formatos.
    Mantiene nombres de mes (no borra letras). Devuelve columna como pl.Date.
    """
    if date_formats is None:
        date_formats = ["%d/%m/%Y", "%Y %b %d %I:%M:%S %p", "%Y-%m-%d", "%d-%b-%Y %H:%M:%S"]
    exprs = [
        pl.col(col_name).str.strptime(pl.Datetime, format=fmt, strict=False)
        for fmt in date_formats
    ]
    return df.with_columns(
        pl.coalesce(exprs).cast(pl.Date).alias(col_name)
    )

def FiltradoYReordenarColumnas(df, ColumnasUsadas,NuevosNombresColumnas,Reorden):
    df_clean=df.select(ColumnasUsadas)
    Equivalencias=listas_a_diccionario(ColumnasUsadas, NuevosNombresColumnas)
    df_clean=df_clean.rename(Equivalencias)
    df_clean=df_clean.select(Reorden)
    return df_clean.collect()

def transform_col_categorical(df: pl.DataFrame, col_name: str,
                            data_null_value: Optional[Union[str, Iterable[str]]] = None) -> pl.DataFrame:
    """
    Convierte una columna a Categorical y opcionalmente trata ciertos valores como null.
    - data_null_value puede ser:
      * None -> no reemplazo explícito
      * una cadena (p. ej. '') -> ese valor se convierte a null antes de castear
      * un iterable de cadenas -> cualquiera de esos se convierte a null
    """
    # imprimir valores iniciales (útil para debug)
    #print("valores iniciales:",col_name, len(set(df[col_name].to_list())), set(df[col_name].to_list()))
    if  len(set(df[col_name].to_list())) >20 and  len(set(df[col_name].to_list())) <10000:
        print(f"Columna '{col_name}' tiene {len(set(df[col_name].to_list()))} valores únicos.")

    # si nos pasan múltiples valores a tratar como null, normalizamos a conjunto
    if data_null_value is not None:
        if isinstance(data_null_value, str):
            null_set = {data_null_value}
        else:
            # asume iterable (list/tuple/set) de valores
            null_set = set(data_null_value)

        # crear una expresión que reemplaza si el valor está en null_set
        expr = pl.when(pl.col(col_name).is_in(list(null_set))).then(pl.lit(None)).otherwise(pl.col(col_name)).alias(col_name)
        df = df.with_columns(expr)

    # ahora casteamos a categórico (permitiendo nulls)
    df = df.with_columns(pl.col(col_name).cast(pl.String))

    # debug: mostrar valores después
    if  len(set(df[col_name].to_list())) >20 and  len(set(df[col_name].to_list())) <10000:
        print(f"Columna '{col_name}' tiene {len(set(df[col_name].to_list()))} valores únicos.")

        print("valores después:", df.select(pl.col(col_name)).to_series().unique().to_list())
    #print("dtype:", df[col_name].dtype)

    return df
    

In [10]:
ColumnasUsadasContrato=['ID Contrato', 'Referencia del Contrato','Nombre Entidad', 'Nit Entidad', 'Departamento', 'Ciudad', 'Orden', 'Sector', 'Rama', 'Entidad Centralizada', 'Proceso de Compra',  'Estado Contrato', 'Codigo de Categoria Principal', 'Descripcion del Proceso', 'Tipo de Contrato', 'Modalidad de Contratacion', 'Justificacion Modalidad de Contratacion', 'Fecha de Firma', 'Fecha de Inicio del Contrato', 'Fecha de Fin del Contrato', 'Condiciones de Entrega',  'Documento Proveedor', 'Proveedor Adjudicado', 'Es Grupo', 'Es Pyme', 'Habilita Pago Adelantado', 'Liquidación', 'Obligación Ambiental', 'Obligaciones Postconsumo', 'Reversion', 'Origen de los Recursos', 'Destino Gasto', 'Valor del Contrato', 'Valor de pago adelantado', 'Valor Facturado', 'Valor Pendiente de Pago', 'Valor Pagado', 'Valor Amortizado', 'Valor Pendiente de Amortizacion', 'Valor Pendiente de Ejecucion', 'Saldo CDP', 'Saldo Vigencia', 'EsPostConflicto', 'Dias adicionados', 'Puntos del Acuerdo', 'Pilares del Acuerdo', 'URLProceso', 'Nacionalidad Representante Legal', 'Domicilio Representante Legal', 'Identificación Representante Legal', 'Género Representante Legal', 'Presupuesto General de la Nacion – PGN', 'Sistema General de Participaciones', 'Sistema General de Regalías', 'Recursos Propios (Alcaldías, Gobernaciones y Resguardos Indígenas)', 'Recursos de Credito', 'Recursos Propios', 'Ultima Actualizacion', 'Codigo Entidad', 'Codigo Proveedor', 'Fecha Inicio Liquidacion', 'Fecha Fin Liquidacion', 'Objeto del Contrato', 'Duración del contrato', 'El contrato puede ser prorrogado', 'Fecha de notificación de prorrogación', 'Número de documento Ordenador del gasto', 'Número de documento supervisor', 'Número de documento Ordenador de Pago', 'Documentos Tipo', 'Descripcion Documentos Tipo']
NuevosNombresColumnasContrato=['IdContrato', 'RefContrato','NombreEntidad', 'NitEntidad', 'Departamento', 'Ciudad', 'Orden', 'Sector', 'Rama', 'EntidadCentralizada', 'ProcesoDeCompra',  'EstadoContrato', 'CodigoDeCategoriaPrincipal', 'DescripcionDelProceso', 'TipodeContrato', 'ModalidadDeContratacion', 'JustificacionModalidadContratacion', 'FechaDeFirma', 'FechaDeInicioContrato', 'FechaDeFinContrato', 'CondicionesDeEntrega',  'DocumentoProveedor', 'ProveedorAdjudicado', 'EsGrupo', 'EsPyme', 'HabilitaPagoAdelantado', 'Liquidación', 'ObligaciónAmbiental', 'ObligacionesPostconsumo', 'Reversion', 'OrigendelosRecursos', 'DestinoGasto', 'ValordelContrato', 'ValorDePagoAdelantado', 'ValorFacturado', 'ValorPendienteDePago', 'ValorPagado', 'ValorAmortizado', 'ValorPendientedeAmortizacion', 'ValorPendienteDeEjecucion', 'SaldoCDP', 'SaldoVigencia', 'EsPostConflicto', 'DiasAdicionados', 'PuntosDelAcuerdo', 'PilaresDelAcuerdo', 'URLProceso', 'NacionalidadRepresentanteLegal', 'DomicilioRepresentanteLegal', 'IdentificaciónRepresentanteLegal', 'GéneroRepresentanteLegal', 'PresupuestoGeneraldelaNacion', 'SistemaGeneralDeParticipaciones', 'SistemaGeneralDeRegalías', 'RecursosPropiosAlcaldiasGobernacionesResguardosIndígenas', 'RecursosDeCredito', 'RecursosPropios', 'UltimaActualizacion', 'CodigoEntidad', 'CodigoProveedor', 'FechaInicioLiquidacion', 'FechaFinLiquidacion', 'ObjetoDelContrato', 'DuracióndelContrato', 'ElContratoPuedeSerProrrogado', 'FechaDeNotificaciónDeProrrogación', 'NúmeroDeDocumentoOrdenadorDelGasto', 'NúmeroDeDocumentoSupervisor', 'NúmeroDeDocumentoOrdenadordePago', 'DocumentosTipo', 'DescripcionDocumentosTipo']
ReordenContrato=[#Datos del contrato
                            'IdContrato', 'RefContrato', 'EstadoContrato', 'CodigoDeCategoriaPrincipal','TipodeContrato','ModalidadDeContratacion','JustificacionModalidadContratacion','ObjetoDelContrato',
                            'URLProceso', 
                            #Datos de fechas y tiempos del contrato
                            'DuracióndelContrato', 'ElContratoPuedeSerProrrogado', 'FechaDeNotificaciónDeProrrogación', 
                            'FechaDeFirma', 'FechaDeInicioContrato', 'FechaDeFinContrato', 
                            'DiasAdicionados', 
                            'FechaInicioLiquidacion', 'FechaFinLiquidacion', 
                            #Datos de la entidad contratante
                            
                            'NombreEntidad', 'NitEntidad', 'EntidadCentralizada',
                            
                            #Datos del proveedor
                            'CodigoProveedor',
                            'DocumentoProveedor', 'ProveedorAdjudicado', 'EsGrupo', 'EsPyme',
                            'NacionalidadRepresentanteLegal', 'DomicilioRepresentanteLegal', 'IdentificaciónRepresentanteLegal', 'GéneroRepresentanteLegal',

                            #Datos de documentos    
                            'NúmeroDeDocumentoOrdenadorDelGasto', 'NúmeroDeDocumentoSupervisor', 
                            'NúmeroDeDocumentoOrdenadordePago',
                            #Ubicación
                            'Departamento', 'Ciudad', 
                            #Datos generales
                            'Orden', 'Sector', 'Rama',

                            #Datos del proceso de compra y condiciones
                            'ProcesoDeCompra','DescripcionDelProceso', 
                            'CondicionesDeEntrega',  
                            'HabilitaPagoAdelantado', 'Liquidación', 
                            'ObligaciónAmbiental', 'ObligacionesPostconsumo', 
                            'Reversion', 
                            'EsPostConflicto',
                            'PuntosDelAcuerdo', 'PilaresDelAcuerdo', 
                            #Datos financieros
                            'OrigendelosRecursos', 'DestinoGasto', 
                            'ValordelContrato', 'ValorDePagoAdelantado', 'ValorFacturado', 'ValorPendienteDePago', 'ValorPagado', 'ValorAmortizado', 'ValorPendientedeAmortizacion', 'ValorPendienteDeEjecucion', 'SaldoCDP', 'SaldoVigencia', 
                            #Datos presupuestales
                            'PresupuestoGeneraldelaNacion', 'SistemaGeneralDeParticipaciones', 'SistemaGeneralDeRegalías', 'RecursosPropiosAlcaldiasGobernacionesResguardosIndígenas', 'RecursosDeCredito', 'RecursosPropios',
                            #Metadatos
                            'UltimaActualizacion', 
                            'DocumentosTipo',
                            'DescripcionDocumentosTipo']

ContratosClean=FiltradoYReordenarColumnas(ContratosE, ColumnasUsadasContrato,NuevosNombresColumnasContrato,ReordenContrato)


ColumnasUsadasAdiciones=[ 'ID_Contrato', 'Identificador','Tipo', 'Descripcion', 'FechaRegistro']
NuevosNombresColumnasAdiciones=['IdContrato', 'Identificador','Tipo', 'Descripcion', 'FechaRegistro']
ReordenAdiciones=[#contrato al que pertenece la adición
                            'IdContrato', 
                            #Datos de la adición
                            'Identificador','Tipo', 'Descripcion', 'FechaRegistro']

AdicionesClean=FiltradoYReordenarColumnas(Adiciones, ColumnasUsadasAdiciones,NuevosNombresColumnasAdiciones,ReordenAdiciones)


ColumnasUsadasEjecucion=['Identificador del Contrato', 'Tipo de Ejecucion', 'Nombre del Plan', 'Fecha de Entrega Esperada', 'Porcentaje de Avance Esperado', 'Fecha de Entrega Real', 'Porcentaje de avance real', 'Estado del contrato', 'Referencia de articulos', 'Descripción', 'Unidad', 'Cantidad adjudicada', 'Cantidad planeada', 'Cantidad Recibida', 'Cantidad por Recibir', 'Fecha Creacion']
NuevosNombresColumnasEjecucion=['IdContrato', 'TipoDeEjecucion', 'NombreDelPlan', 'FechaDeEntregaEsperada', 'PorcentajeDeAvanceEsperado', 'FechaDeEntregaReal', 'PorcentajedeAvanceReal', 'EstadoDelContrato', 'ReferenciaDeArticulos', 'Descripción', 'Unidad', 'CantidadAdjudicada', 'CantidadPlaneada', 'CantidadRecibida', 'CantidadPorRecibir', 'FechaCreacion']
ReordenEjecucion=[#contrato al que pertenece la ejecución
                            'IdContrato', 
                            #Datos de la ejecución
                            'TipoDeEjecucion', 'NombreDelPlan', 
                            #Fechas y avances 
                            'FechaDeEntregaEsperada', 'PorcentajeDeAvanceEsperado', 
                            'FechaDeEntregaReal', 'PorcentajedeAvanceReal',
                            
                            'EstadoDelContrato', 
                            'ReferenciaDeArticulos', 'Descripción', 'Unidad', 
                            
                            #Informacion financiera
                            'CantidadAdjudicada', 'CantidadPlaneada',
                            'CantidadRecibida', 'CantidadPorRecibir', 
                            'FechaCreacion']
EjecucionClean=FiltradoYReordenarColumnas(Ejecucion, ColumnasUsadasEjecucion,NuevosNombresColumnasEjecucion,ReordenEjecucion)

#GarantiasClean=Garantias['ID Contrato', 'Aseguradora', 'Asegurado', 'Beneficiario', 'FechaDeCreacionPoliza', 'FechaEnvioPoliza', 'FechaFinPoliza', 'LadoPoliza', 'Estado', 'TipoPoliza', 'SubTipoPoliza', 'Valor', 'Fecha de Creacion']


In [8]:
#Datos de sancionados

import os
import json
import pandas as pd
from sodapy import Socrata
pwd=os.path.dirname("app/private/experiment_config.json")
def extractConfig(nameModel="SystemData",relPath=os.path.join(pwd,"experiment_config.json"),dataOut="keyantrophics"):
    configPath=os.path.join(os.getcwd(),relPath)
    with open(configPath, 'r', encoding='utf-8') as file:
        config = json.load(file)[nameModel]
    Output= config[dataOut]
    return Output
claveApiSocrata=extractConfig(nameModel="SocratesApi",dataOut="claveAppApi")
url=extractConfig(nameModel="SystemData",dataOut="urlApi",relPath=os.path.join(pwd,"experiment_config.json"))


# # Unauthenticated client only works with public data sets. Note 'None'
# # in place of application token, and no username or password:
client = Socrata("www.datos.gov.co", claveApiSocrata)

SancionesSecopI="4n4q-k399"
AntededentesSiri="iaeu-rcn6"




for item in client.get_all(SancionesSecopI):
    print(item)

{'nombre_entidad': 'ADMINISTRADORA DE LOS RECURSOS DEL SISTEMA GENERAL DE SEGURIDAD SOCIAL EN SALUD', 'nit_entidad': '901037916', 'nivel': 'NACIONAL', 'orden': 'NACIONAL DESCENTRALIZADO', 'municipio': 'Bogotá D.C.', 'numero_de_resolucion': 'RESOLUCION 41549 DE 2019', 'documento_contratista': '1067811412', 'nombre_contratista': 'JORGE HUMBERTO FERIAS MANJARRES', 'numero_de_contrato': 'ADRES-CTO-137-2019', 'valor_sancion': '3797492', 'fecha_de_publicacion': '2019-11-07T00:00:00.000', 'fecha_de_firmeza': '2019-11-14T00:00:00.000', 'fecha_de_cargue': '2019-11-15T00:00:00.000', 'ruta_de_proceso': 'https://www.contratos.gov.co/consultas/detalleProcesoAACS.do?numProcAACS=26189079'}
{'nombre_entidad': 'AGENCIA LOGÍSTICA DE LAS FUERZAS MILITARES (ALFM)', 'nit_entidad': '899999162', 'nivel': 'NACIONAL', 'orden': 'NACIONAL DESCENTRALIZADO', 'municipio': 'Acacías', 'numero_de_resolucion': '070', 'documento_contratista': '9005939217', 'nombre_contratista': 'JL INGENIEROS OBRAS Y SUMINISTROS SAS', '

In [42]:

import requests
def cargar_estadistica(campo, seccion, variable, valor, texto_visible=""):
    payload = {"campo":campo,
    "seccion":seccion,
    "variable":variable,
    "texto_visible":texto_visible,
    "valor":valor}
    response = requests.post(url="http://127.0.0.1:8000/estadisticas", json=payload)
    print(response.text)

In [1]:
import os
import json
import pandas as pd
from sodapy import Socrata
pwd=os.path.dirname("app/private/experiment_config.json")
def extractConfig(nameModel="SystemData",relPath=os.path.join(pwd,"experiment_config.json"),dataOut="keyantrophics"):
    configPath=os.path.join(os.getcwd(),relPath)
    with open(configPath, 'r', encoding='utf-8') as file:
        config = json.load(file)[nameModel]
    Output= config[dataOut]
    return Output
claveApiSocrata=extractConfig(nameModel="SocratesApi",dataOut="claveAppApi")
url=extractConfig(nameModel="SystemData",dataOut="urlApi",relPath=os.path.join(pwd,"experiment_config.json"))


# # Unauthenticated client only works with public data sets. Note 'None'
# # in place of application token, and no username or password:
client = Socrata("www.datos.gov.co", claveApiSocrata)
# #adiciones

adicionContr=client.get("cb9c-h8sn" ,where="id_contrato == 'CO1.PCCNTR.7438117'")#, order="magnitude DESC", exclude_system_fields=False)
# #ContratosE
Contr=client.get("jbjy-vk9h" ,where="id_contrato == 'CO1.PCCNTR.7438117'")
# #ejecucion
ejecucionContr=client.get("mfmm-jqmq" ,where="identificadorcontrato == 'CO1.PCCNTR.1000001'")

AllData={'Adiciones':adicionContr, 'ContratosE':Contr, 'Ejecucion':ejecucionContr}


In [4]:
Contr

[{'nombre_entidad': 'CENAC PUENTE ARANDA+',
  'nit_entidad': '830039548',
  'departamento': 'Distrito Capital de Bogotá',
  'ciudad': 'Bogotá',
  'localizaci_n': 'Colombia, Bogotá,  Bogotá',
  'orden': 'Nacional',
  'sector': 'defensa',
  'rama': 'Ejecutivo',
  'entidad_centralizada': 'Centralizada',
  'proceso_de_compra': 'CO1.BDOS.7502613',
  'id_contrato': 'CO1.PCCNTR.7438117',
  'referencia_del_contrato': '035-COADE-DICRE-CENAC PUENTE ARANDA - 2025',
  'estado_contrato': 'Modificado',
  'codigo_de_categoria_principal': 'V1.80111600',
  'descripcion_del_proceso': 'PRESTACIÓN DE SERVICIOS PROFESIONALES COMO INGENIERO QUIMICO COMO ASESOR DE DIRECCIÓN DE CALIDAD PARA EL LABORATORIO CONTROL DE CALIDAD DEL EJÉRCITO - LACCE DEL BATALLÓN DE MANTENIMIENTO',
  'tipo_de_contrato': 'Prestación de servicios',
  'modalidad_de_contratacion': 'Contratación directa',
  'justificacion_modalidad_de': 'Servicios profesionales y apoyo a la gestión',
  'fecha_de_firma': '2025-02-07T00:00:00.000',
  'fec

In [ ]:
#seCUENCIA 
response = requests.post(url="http://127.0.0.1:8000/contratos/",json=Contr[0])
print(response.text)

{"detail":"El id_contrato 'CO1.PCCNTR.7438117' ya existe"}


In [44]:
adicionContr

[{'identificador': 'CO1.CTRMOD.20082692',
  'id_contrato': 'CO1.PCCNTR.7438117',
  'tipo': 'MODIFICACION GENERAL',
  'descripcion': 'MODIFICATORIO 1 (ADICIoN Y PRoRROGA) AL CONTRATO 035 DE 2025',
  'fecharegistro': '2025-09-02T00:00:00.000'},
 {'identificador': 'CO1.CTRMOD.20082692',
  'id_contrato': 'CO1.PCCNTR.7438117',
  'tipo': 'MODIFICACION GENERAL',
  'descripcion': 'MODIFICATORIO 1 (ADICIoN Y PRoRROGA) AL CONTRATO 035 DE 2025',
  'fecharegistro': '2025-09-02T00:00:00.000'},
 {'identificador': 'CO1.CTRMOD.19554481',
  'id_contrato': 'CO1.PCCNTR.7438117',
  'tipo': 'CESION',
  'descripcion': 'CESIoN SOLICITADA POR SERGIO MORA',
  'fecharegistro': '2025-07-08T00:00:00.000'},
 {'identificador': 'CO1.CTRMOD.19554481',
  'id_contrato': 'CO1.PCCNTR.7438117',
  'tipo': 'CESION',
  'descripcion': 'CESIoN SOLICITADA POR SERGIO MORA',
  'fecharegistro': '2025-07-08T00:00:00.000'},
 {'identificador': 'CO1.CTRMOD.20082692',
  'id_contrato': 'CO1.PCCNTR.7438117',
  'tipo': 'MODIFICACION GENER

In [ ]:
#listo
from datetime import datetime
import requests
urlt=extractConfig(nameModel="SystemData",dataOut="urlApi")+"adiciones/"
for i in adicionContr:
    t=requests.post(url=urlt,json=i)
    print(t)




<Response [201]>
<Response [201]>
<Response [201]>
<Response [201]>
<Response [201]>
<Response [201]>
<Response [201]>
<Response [201]>
<Response [201]>


In [33]:
AllData["ContratosE"]

[{'nombre_entidad': 'CENAC PUENTE ARANDA+',
  'nit_entidad': '830039548',
  'departamento': 'Distrito Capital de Bogotá',
  'ciudad': 'Bogotá',
  'localizaci_n': 'Colombia, Bogotá,  Bogotá',
  'orden': 'Nacional',
  'sector': 'defensa',
  'rama': 'Ejecutivo',
  'entidad_centralizada': 'Centralizada',
  'proceso_de_compra': 'CO1.BDOS.7502613',
  'id_contrato': 'CO1.PCCNTR.7438117',
  'referencia_del_contrato': '035-COADE-DICRE-CENAC PUENTE ARANDA - 2025',
  'estado_contrato': 'Modificado',
  'codigo_de_categoria_principal': 'V1.80111600',
  'descripcion_del_proceso': 'PRESTACIÓN DE SERVICIOS PROFESIONALES COMO INGENIERO QUIMICO COMO ASESOR DE DIRECCIÓN DE CALIDAD PARA EL LABORATORIO CONTROL DE CALIDAD DEL EJÉRCITO - LACCE DEL BATALLÓN DE MANTENIMIENTO',
  'tipo_de_contrato': 'Prestación de servicios',
  'modalidad_de_contratacion': 'Contratación directa',
  'justificacion_modalidad_de': 'Servicios profesionales y apoyo a la gestión',
  'fecha_de_firma': '2025-02-07T00:00:00.000',
  'fec

In [13]:
Contr[0].keys()

dict_keys(['nombre_entidad', 'nit_entidad', 'departamento', 'ciudad', 'localizaci_n', 'orden', 'sector', 'rama', 'entidad_centralizada', 'proceso_de_compra', 'id_contrato', 'referencia_del_contrato', 'estado_contrato', 'codigo_de_categoria_principal', 'descripcion_del_proceso', 'tipo_de_contrato', 'modalidad_de_contratacion', 'justificacion_modalidad_de', 'fecha_de_firma', 'fecha_de_inicio_del_contrato', 'fecha_de_fin_del_contrato', 'condiciones_de_entrega', 'tipodocproveedor', 'documento_proveedor', 'proveedor_adjudicado', 'es_grupo', 'es_pyme', 'habilita_pago_adelantado', 'liquidaci_n', 'obligaci_n_ambiental', 'obligaciones_postconsumo', 'reversion', 'origen_de_los_recursos', 'destino_gasto', 'valor_del_contrato', 'valor_de_pago_adelantado', 'valor_facturado', 'valor_pendiente_de_pago', 'valor_pagado', 'valor_amortizado', 'valor_pendiente_de', 'valor_pendiente_de_ejecucion', 'estado_bpin', 'c_digo_bpin', 'anno_bpin', 'saldo_cdp', 'saldo_vigencia', 'espostconflicto', 'dias_adicionados

In [ ]:
#Listo
urlt=url+"contratos/"
import requests
t=requests.post(url=urlt,json=Contr[0])
print(t.text)

{"detail":"El id_contrato 'CO1.PCCNTR.7438117' ya existe"}


In [11]:
urlt

'http://127.0.0.1:8000/contratos/'

In [8]:
os.path.join(pwd,"experiment_config.json")

'app/private/experiment_config.json'

In [ ]:
claves_a_seleccionar=['nombre_entidad',  'departamento',
  'ciudad',
  'orden',
  'sector',
  'rama',
  'entidad_centralizada']
entidad = {k: v for k, v in AllData["ContratosE"][0].items() if k in claves_a_seleccionar}

claves_a_seleccionar=[  'documento_proveedor',
  'proveedor_adjudicado',
  'es_grupo',
  'es_pyme']
proveedor = {k: v for k, v in AllData["ContratosE"][0].items() if k in claves_a_seleccionar}


claves_a_seleccionar=['nombre_representante_legal',
  'identificaci_n_representante_legal']
representante_legal = {k: v for k, v in AllData["ContratosE"][0].items() if k in claves_a_seleccionar}

claves_a_seleccionar=['nombre_ordenador_del_gasto',
'n_mero_de_documento_ordenador_del_gasto']
ordenador_gasto = {k: v for k, v in AllData["ContratosE"][0].items() if k in claves_a_seleccionar}


claves_a_seleccionar=['nombre_supervisor',
  'n_mero_de_documento_supervisor']
supervisor = {k: v for k, v in AllData["ContratosE"][0].items() if k in claves_a_seleccionar}

supervisor={"nombre": supervisor['nombre_supervisor'],
"documento": supervisor['n_mero_de_documento_supervisor']}

proveedor={"documento": proveedor['documento_proveedor'],"nombre": proveedor['proveedor_adjudicado'], "es_grupo": proveedor['es_grupo'], "es_pyme": proveedor['es_pyme']}

representante_legal={"nombre": representante_legal['nombre_representante_legal'],
"documento": representante_legal['identificaci_n_representante_legal']}

ordenador_gasto={"nombre": ordenador_gasto['nombre_ordenador_del_gasto'],
"documento": ordenador_gasto['n_mero_de_documento_ordenador_del_gasto']}


In [47]:
entidad

{'nombre_entidad': 'CENAC PUENTE ARANDA+',
 'departamento': 'Distrito Capital de Bogotá',
 'ciudad': 'Bogotá',
 'orden': 'Nacional',
 'sector': 'defensa',
 'rama': 'Ejecutivo',
 'entidad_centralizada': 'Centralizada'}

In [12]:
ContratosClean2=ContratosClean
for i in [
    "DocumentoProveedor",
    "IdentificaciónRepresentanteLegal",
    "NúmeroDeDocumentoOrdenadorDelGasto",
    "NúmeroDeDocumentoSupervisor",
    "NúmeroDeDocumentoOrdenadordePago",
    "ValordelContrato",
    "ValorDePagoAdelantado",
    "ValorFacturado",
    "ValorPendienteDePago",
    "ValorPagado",
    "ValorAmortizado",
    "ValorPendientedeAmortizacion",
    "ValorPendienteDeEjecucion",
    "SaldoCDP",
    "SaldoVigencia",
    "PresupuestoGeneraldelaNacion",
    "SistemaGeneralDeParticipaciones",
    "SistemaGeneralDeRegalías",
    "RecursosPropiosAlcaldiasGobernacionesResguardosIndígenas",
    "RecursosDeCredito",
    "RecursosPropios","CodigoEntidad","NitEntidad"
]:
    print(i)
    ContratosClean2 = clean_col_integer(ContratosClean2, i)

for i in ["FechaDeFirma",
"FechaDeInicioContrato"	,
"FechaDeFinContrato",
"FechaDeNotificaciónDeProrrogación",
"FechaInicioLiquidacion",	
"FechaFinLiquidacion",
"UltimaActualizacion"]:
    print(i)
    ContratosClean2 = clean_col_date(ContratosClean2, i)


for i in ["DescripcionDocumentosTipo","DuracióndelContrato","NacionalidadRepresentanteLegal",
        "Departamento","Ciudad","HabilitaPagoAdelantado","ObjetoDelContrato","DomicilioRepresentanteLegal","GéneroRepresentanteLegal",
        "CondicionesDeEntrega","DestinoGasto"]:
    print(i)
    ContratosClean2 = transform_col_categorical(ContratosClean2, i, data_null_value=['','NA','N/A','N.A.','null','Null','NULL','No definido','No Definido'])

DocumentoProveedor
IdentificaciónRepresentanteLegal
NúmeroDeDocumentoOrdenadorDelGasto
NúmeroDeDocumentoSupervisor
NúmeroDeDocumentoOrdenadordePago
ValordelContrato
ValorDePagoAdelantado
ValorFacturado
ValorPendienteDePago
ValorPagado
ValorAmortizado
ValorPendientedeAmortizacion
ValorPendienteDeEjecucion
SaldoCDP
SaldoVigencia
PresupuestoGeneraldelaNacion
SistemaGeneralDeParticipaciones
SistemaGeneralDeRegalías
RecursosPropiosAlcaldiasGobernacionesResguardosIndígenas
RecursosDeCredito
RecursosPropios
CodigoEntidad
NitEntidad
FechaDeFirma
FechaDeInicioContrato
FechaDeFinContrato
FechaDeNotificaciónDeProrrogación
FechaInicioLiquidacion
FechaFinLiquidacion
UltimaActualizacion
DescripcionDocumentosTipo
DuracióndelContrato
NacionalidadRepresentanteLegal
Departamento
Columna 'Departamento' tiene 31 valores únicos.
Columna 'Departamento' tiene 31 valores únicos.
valores después: ['Huila', 'San Andrés, Providencia y Santa Catalina', 'Atlántico', None, 'Amazonas', 'Caldas', 'Risaralda', 'Sucre'

In [13]:
for i in ContratosClean2.columns:
    print(i,ContratosClean2[i].null_count(),list(ContratosClean2[i].unique()))

IdContrato 0 ['CO1.PCCNTR.1003002', 'CO1.PCCNTR.1004005', 'CO1.PCCNTR.1002939', 'CO1.PCCNTR.1003036', 'CO1.PCCNTR.1003051', 'CO1.PCCNTR.1003057', 'CO1.PCCNTR.1001015', 'CO1.PCCNTR.1001303', 'CO1.PCCNTR.1002953', 'CO1.PCCNTR.1001628', 'CO1.PCCNTR.1003027', 'CO1.PCCNTR.1003029', 'CO1.PCCNTR.1000604', 'CO1.PCCNTR.1000301', 'CO1.PCCNTR.1002911', 'CO1.PCCNTR.1000907', 'CO1.PCCNTR.100321', 'CO1.PCCNTR.1002724', 'CO1.PCCNTR.1000502', 'CO1.PCCNTR.1002731', 'CO1.PCCNTR.1002920', 'CO1.PCCNTR.1001030', 'CO1.PCCNTR.1002707', 'CO1.PCCNTR.1002957', 'CO1.PCCNTR.1002804', 'CO1.PCCNTR.1001218', 'CO1.PCCNTR.1002101', 'CO1.PCCNTR.1002732', 'CO1.PCCNTR.1003105', 'CO1.PCCNTR.1002708', 'CO1.PCCNTR.1003018', 'CO1.PCCNTR.1002910', 'CO1.PCCNTR.1001104', 'CO1.PCCNTR.1002905', 'CO1.PCCNTR.1001013', 'CO1.PCCNTR.1003802', 'CO1.PCCNTR.1001130', 'CO1.PCCNTR.1001121', 'CO1.PCCNTR.1002402', 'CO1.PCCNTR.1002713', 'CO1.PCCNTR.1002943', 'CO1.PCCNTR.1003037', 'CO1.PCCNTR.100329', 'CO1.PCCNTR.1001111', 'CO1.PCCNTR.1002712'

In [13]:
ContratosClean2.columns

['IdContrato',
 'RefContrato',
 'EstadoContrato',
 'CodigoDeCategoriaPrincipal',
 'TipodeContrato',
 'ModalidadDeContratacion',
 'JustificacionModalidadContratacion',
 'ObjetoDelContrato',
 'URLProceso',
 'DuracióndelContrato',
 'ElContratoPuedeSerProrrogado',
 'FechaDeNotificaciónDeProrrogación',
 'FechaDeFirma',
 'FechaDeInicioContrato',
 'FechaDeFinContrato',
 'DiasAdicionados',
 'FechaInicioLiquidacion',
 'FechaFinLiquidacion',
 'NombreEntidad',
 'NitEntidad',
 'EntidadCentralizada',
 'CodigoProveedor',
 'DocumentoProveedor',
 'ProveedorAdjudicado',
 'EsGrupo',
 'EsPyme',
 'NacionalidadRepresentanteLegal',
 'DomicilioRepresentanteLegal',
 'IdentificaciónRepresentanteLegal',
 'GéneroRepresentanteLegal',
 'NúmeroDeDocumentoOrdenadorDelGasto',
 'NúmeroDeDocumentoSupervisor',
 'NúmeroDeDocumentoOrdenadordePago',
 'Departamento',
 'Ciudad',
 'Orden',
 'Sector',
 'Rama',
 'ProcesoDeCompra',
 'DescripcionDelProceso',
 'CondicionesDeEntrega',
 'HabilitaPagoAdelantado',
 'Liquidación',
 'Ob

In [ ]:
import matplotlib.pyplot as plt
def make_histogram(df,columna=""):
    plt.title("Histograma de "+columna)
    plt.hist(df[columna].drop_nulls().to_list())
    plt.show()
    
for i in ContratosClean2.columns:
    make_histogram(ContratosClean2,i)

In [ ]:
from models.db import db

#for row in conteos:
#    print(f"ID Contrato duplicado: {row.contratos.id_contrato}, Aparece: {row[resultado]} veces")

# Crear un diccionario con los conteos por NIT
# Encontrar nit_entidad con múltiples contratos
resultado = db.contratos.nit_entidad.count()
conteos = db(db.contratos.nit_entidad != None).select(
    db.contratos.nit_entidad,
    resultado,
    groupby=db.contratos.nit_entidad,
    having=resultado > 0,  # Solo los que tienen más de un contrato
    orderby=~resultado
)
resultadoProv = db.contratos.documento_proveedor.count()
conteosProv = db(db.contratos.documento_proveedor != None).select(
    db.contratos.documento_proveedor,
    resultadoProv,
    groupby=db.contratos.documento_proveedor,
    having=resultado > 0,  # Solo los que tienen más de un contrato
    orderby=~resultado
)

for row in conteos:
    nitActual=row.contratos.nit_entidad
    
    dataEntidad=db(db.entidades.nit_entidad == nitActual).select().last()
    try:
        { "id": nitActual, "name":dataEntidad.nombre_entidad,"departamento":dataEntidad.departamento,"url":"","color":'#6da2c4',"size":{row[resultado]},"cap":0})
        
    except:
        pass
        

for row in conteosProv:
    docActual=row.contratos.documento_proveedor
    dataProv=db(db.proveedoresypersonas.documento == docActual).select().last()
    try:
        print(row.values())
        print(docActual,{ "id": docActual, "name":dataProv.nombre,"es_pyme":dataProv.es_pyme,"es_grupo":dataProv.es_grupo,"url":"","color":"#1dc96a","size":row[resultadoProv],"cap":0})
        
    except:
        print(docActual)

for 


dict_values([<Row {'documento_proveedor': '860524654'}>, <Row {'COUNT("contratos"."documento_proveedor")': 11}>])
860524654 {'id': '860524654', 'name': 'Aseguradora Solidaria de Colombia Entidad Cooperativa.', 'es_pyme': 'No', 'es_grupo': 'No', 'url': '', 'color': '#1dc96a', 'size': 11, 'cap': 0}
dict_values([<Row {'documento_proveedor': '860002400'}>, <Row {'COUNT("contratos"."documento_proveedor")': 9}>])
860002400 {'id': '860002400', 'name': 'LA PREVISORA S.A. COMPAÑÍA DE SEGUROS', 'es_pyme': 'No', 'es_grupo': 'No', 'url': '', 'color': '#1dc96a', 'size': 9, 'cap': 0}
dict_values([<Row {'documento_proveedor': '830001113'}>, <Row {'COUNT("contratos"."documento_proveedor")': 8}>])
830001113 {'id': '830001113', 'name': 'IMPRENTA NACIONAL DE COLOMBIA', 'es_pyme': 'No', 'es_grupo': 'No', 'url': '', 'color': '#1dc96a', 'size': 8, 'cap': 0}
dict_values([<Row {'documento_proveedor': '900204272'}>, <Row {'COUNT("contratos"."documento_proveedor")': 5}>])
900204272 {'id': '900204272', 'name': '

In [ ]:
def generar_nodos_y_enlaces():
    """
    Genera dos listas:
    1. nodos: Lista de diccionarios con entidades y proveedores
    2. enlaces: Lista de diccionarios con las relaciones entre entidades y proveedores
    """
    
    nodos = []
    enlaces = []
    enlaces_dict = {}  # Para agrupar enlaces y sumar valores
    
    # ============= PROCESAR ENTIDADES =============
    resultado = db.contratos.nit_entidad.count()
    suma_valor = db.contratos.valor_contrato.sum()
    
    conteos = db(db.contratos.nit_entidad != None).select(
        db.contratos.nit_entidad,
        resultado,
        suma_valor,
        groupby=db.contratos.nit_entidad,
        having=resultado > 0,
        orderby=~resultado
    )
    
    for row in conteos:
        nitActual = row.contratos.nit_entidad
        
        # Buscar datos de la entidad
        dataEntidad = db(db.entidades.nit_entidad == nitActual).select().last()
        
        try:
            nodo_entidad = {
                "id": nitActual,
                "name": dataEntidad.nombre_entidad,
                "departamento": dataEntidad.departamento,
                "tipo": "entidad",
                "url": "",
                "color": '#6da2c4',
                "size": row[resultado],
                "valor_contrato": float(row[suma_valor] or 0)
            }
            nodos.append(nodo_entidad)
        except:
            # Si no existe en tabla entidades, usar datos del contrato
            dataContrato = db(db.contratos.nit_entidad == nitActual).select().first()
            if dataContrato:
                nodo_entidad = {
                    "id": nitActual,
                    "name": dataContrato.nombre_entidad or "Entidad Desconocida",
                    "departamento": dataContrato.departamento or "",
                    "tipo": "entidad",
                    "url": "",
                    "color": '#6da2c4',
                    "size": row[resultado],
                    "valor_contrato": float(row[suma_valor] or 0)
                }
                nodos.append(nodo_entidad)
    
    # ============= PROCESAR PROVEEDORES =============
    resultadoProv = db.contratos.documento_proveedor.count()
    suma_valor_prov = db.contratos.valor_contrato.sum()
    
    conteosProv = db(db.contratos.documento_proveedor != None).select(
        db.contratos.documento_proveedor,
        resultadoProv,
        suma_valor_prov,
        groupby=db.contratos.documento_proveedor,
        having=resultadoProv > 0,
        orderby=~resultadoProv
    )
    
    for row in conteosProv:
        docActual = row.contratos.documento_proveedor
        
        # Buscar datos del proveedor
        dataProv = db(db.proveedoresypersonas.documento == docActual).select().last()
        
        try:
            nodo_proveedor = {
                "id": docActual,
                "name": dataProv.nombre,
                "es_pyme": dataProv.es_pyme or "No",
                "es_grupo": dataProv.es_grupo or "No",
                "tipo": "proveedor",
                "url": "",
                "color": "#1dc96a",
                "size": row[resultadoProv],
                "valor_contrato": float(row[suma_valor_prov] or 0)
            }
            nodos.append(nodo_proveedor)
        except:
            # Si no existe en tabla proveedores, usar datos del contrato
            dataContrato = db(db.contratos.documento_proveedor == docActual).select().first()
            if dataContrato:
                nodo_proveedor = {
                    "id": docActual,
                    "name": dataContrato.proveedor_adjudicado or "Proveedor Desconocido",
                    "es_pyme": dataContrato.es_pyme or "No",
                    "es_grupo": dataContrato.es_grupo or "No",
                    "tipo": "proveedor",
                    "url": "",
                    "color": "#1dc96a",
                    "size": row[resultadoProv],
                    "valor_contrato": float(row[suma_valor_prov] or 0)
                }
                nodos.append(nodo_proveedor)
    
    # ============= GENERAR ENLACES (RELACIONES) =============
    # Obtener todas las relaciones entidad-proveedor
    contratos = db(
        (db.contratos.nit_entidad != None) & 
        (db.contratos.documento_proveedor != None)
    ).select(
        db.contratos.nit_entidad,
        db.contratos.documento_proveedor,
        db.contratos.valor_contrato
    )
    
    # Agrupar enlaces y sumar valores
    for contrato in contratos:
        source = contrato.nit_entidad
        target = contrato.documento_proveedor
        identificador = f"{source}_{target}"
        
        if identificador not in enlaces_dict:
            enlaces_dict[identificador] = {
                "source": source,
                "target": target,
                "identificador": identificador,
                "color": "#ff0000",
                "cantidad_contratos": 0,
                "valor_contrato": 0
            }
        
        enlaces_dict[identificador]["cantidad_contratos"] += 1
        enlaces_dict[identificador]["valor_contrato"] += float(contrato.valor_contrato or 0)
    
    # Convertir diccionario de enlaces a lista
    enlaces = list(enlaces_dict.values())
    
    return nodos, enlaces


# ============= USAR LA FUNCIÓN =============
nodos, enlaces = generar_nodos_y_enlaces()

print(f"Total de nodos: {len(nodos)}")
print(f"Total de enlaces: {len(enlaces)}")



Total de nodos: 13482
Total de enlaces: 12280

Primeros 3 nodos:
{'id': '899999034', 'name': 'SENA REGIONAL ANTIOQUIA Grupo Administrativo Complejo Itagüí', 'departamento': 'Antioquia', 'tipo': 'entidad', 'url': '', 'color': '#6da2c4', 'size': 750, 'valor_contrato': 48514769785.0}
{'id': '890399011', 'name': 'SECRETARIA DE EDUCACION DE CALI', 'departamento': 'Valle del Cauca', 'tipo': 'entidad', 'url': '', 'color': '#6da2c4', 'size': 484, 'valor_contrato': 51139404709.0}
{'id': '899999061', 'name': 'SECRETARÍA GENERAL DE LA ALCALDÍA MAYOR DE BOGOTÁ', 'departamento': 'Distrito Capital de Bogotá', 'tipo': 'entidad', 'url': '', 'color': '#6da2c4', 'size': 405, 'valor_contrato': 37807403688.0}

Primeros 3 enlaces:
{'source': '899999061', 'target': '52562597', 'identificador': '899999061_52562597', 'color': '#ff0000', 'cantidad_contratos': 1, 'valor_contrato': 23310505.0}
{'source': '899999102', 'target': '900431716', 'identificador': '899999102_900431716', 'color': '#ff0000', 'cantidad_con

In [60]:
def generar_nodos_y_enlaces(nit_entidad=None, documento_proveedor=None, departamento=None, 
                            fecha_inicio=None, fecha_fin=None, valor_minimo=None, valor_maximo=None):
    """
    Genera dos listas:
    1. nodos: Lista de diccionarios con entidades y proveedores
    2. enlaces: Lista de diccionarios con las relaciones entre entidades y proveedores
    
    Parámetros:
    - nit_entidad: Filtrar por un NIT de entidad específico
    - documento_proveedor: Filtrar por documento de proveedor específico
    - departamento: Filtrar por departamento
    - fecha_inicio: Filtrar contratos desde esta fecha
    - fecha_fin: Filtrar contratos hasta esta fecha
    - valor_minimo: Valor mínimo del contrato
    - valor_maximo: Valor máximo del contrato
    """
    
    nodos = []
    enlaces = []
    enlaces_dict = {}
    
    # ============= CONSTRUIR QUERY BASE =============
    query_base = (db.contratos.id > 0)  # Query inicial siempre verdadera
    
    if nit_entidad:
        query_base &= (db.contratos.nit_entidad == nit_entidad)
    
    if documento_proveedor:
        query_base &= (db.contratos.documento_proveedor == documento_proveedor)
    
    if departamento:
        query_base &= (db.contratos.departamento == departamento)
    
    if fecha_inicio:
        query_base &= (db.contratos.fecha_inicio >= fecha_inicio)
    
    if fecha_fin:
        query_base &= (db.contratos.fecha_fin <= fecha_fin)
    
    if valor_minimo:
        query_base &= (db.contratos.valor_contrato >= valor_minimo)
    
    if valor_maximo:
        query_base &= (db.contratos.valor_contrato <= valor_maximo)
    
    # ============= PROCESAR ENTIDADES =============
    resultado = db.contratos.nit_entidad.count()
    suma_valor = db.contratos.valor_contrato.sum()
    
    query_entidades = query_base & (db.contratos.nit_entidad != None)
    
    conteos = db(query_entidades).select(
        db.contratos.nit_entidad,
        resultado,
        suma_valor,
        groupby=db.contratos.nit_entidad,
        having=resultado > 0,
        orderby=~resultado
    )
    
    for row in conteos:
        nitActual = row.contratos.nit_entidad
        
        # Buscar datos de la entidad
        dataEntidad = db(db.entidades.nit_entidad == nitActual).select().last()
        
        try:
            nodo_entidad = {
                "id": nitActual,
                "name": dataEntidad.nombre_entidad,
                "departamento": dataEntidad.departamento,
                "tipo": "entidad",
                "url": "",
                "color": '#6da2c4',
                "size": row[resultado],
                "valor_contrato": float(row[suma_valor] or 0)
            }
            nodos.append(nodo_entidad)
        except:
            # Si no existe en tabla entidades, usar datos del contrato
            dataContrato = db(db.contratos.nit_entidad == nitActual).select().first()
            if dataContrato:
                nodo_entidad = {
                    "id": nitActual,
                    "name": dataContrato.nombre_entidad or "Entidad Desconocida",
                    "departamento": dataContrato.departamento or "",
                    "tipo": "entidad",
                    "url": "",
                    "color": '#6da2c4',
                    "size": row[resultado],
                    "valor_contrato": float(row[suma_valor] or 0)
                }
                nodos.append(nodo_entidad)
    
    # ============= PROCESAR PROVEEDORES =============
    resultadoProv = db.contratos.documento_proveedor.count()
    suma_valor_prov = db.contratos.valor_contrato.sum()
    
    query_proveedores = query_base & (db.contratos.documento_proveedor != None)
    
    conteosProv = db(query_proveedores).select(
        db.contratos.documento_proveedor,
        resultadoProv,
        suma_valor_prov,
        groupby=db.contratos.documento_proveedor,
        having=resultadoProv > 0,
        orderby=~resultadoProv
    )
    
    for row in conteosProv:
        docActual = row.contratos.documento_proveedor
        
        # Buscar datos del proveedor
        dataProv = db(db.proveedoresypersonas.documento == docActual).select().last()
        
        try:
            nodo_proveedor = {
                "id": docActual,
                "name": dataProv.nombre,
                "es_pyme": dataProv.es_pyme or "No",
                "es_grupo": dataProv.es_grupo or "No",
                "tipo": "proveedor",
                "url": "",
                "color": "#1dc96a",
                "size": row[resultadoProv],
                "valor_contrato": float(row[suma_valor_prov] or 0)
            }
            nodos.append(nodo_proveedor)
        except:
            # Si no existe en tabla proveedores, usar datos del contrato
            dataContrato = db(db.contratos.documento_proveedor == docActual).select().first()
            if dataContrato:
                nodo_proveedor = {
                    "id": docActual,
                    "name": dataContrato.proveedor_adjudicado or "Proveedor Desconocido",
                    "es_pyme": dataContrato.es_pyme or "No",
                    "es_grupo": dataContrato.es_grupo or "No",
                    "tipo": "proveedor",
                    "url": "",
                    "color": "#1dc96a",
                    "size": row[resultadoProv]*9,
                    "valor_contrato": float(row[suma_valor_prov] or 0)
                }
                nodos.append(nodo_proveedor)
    
    # ============= GENERAR ENLACES (RELACIONES) =============
    query_enlaces = query_base & (db.contratos.nit_entidad != None) & (db.contratos.documento_proveedor != None)
    
    contratos = db(query_enlaces).select(
        db.contratos.nit_entidad,
        db.contratos.documento_proveedor,
        db.contratos.valor_contrato
    )
    
    # Agrupar enlaces y sumar valores
    for contrato in contratos:
        source = contrato.nit_entidad
        target = contrato.documento_proveedor
        identificador = f"{source}_{target}"
        
        if identificador not in enlaces_dict:
            enlaces_dict[identificador] = {
                "source": source,
                "target": target,
                "identificador": identificador,
                "color": "#ff0000",
                "cantidad_contratos": 0,
                "valor_contrato": 0
            }
        
        enlaces_dict[identificador]["cantidad_contratos"] += 1
        enlaces_dict[identificador]["valor_contrato"] += float(contrato.valor_contrato or 0)
    
    # Convertir diccionario de enlaces a lista
    enlaces = list(enlaces_dict.values())
    
    return nodos, enlaces


# ============= EJEMPLOS DE USO =============

# 1. Sin filtros (todos los contratos)
nodos, enlaces = generar_nodos_y_enlaces()
print(f"Sin filtros - Nodos: {len(nodos)}, Enlaces: {len(enlaces)}")

# 2. Filtrar por un NIT de entidad específico
nodos, enlaces = generar_nodos_y_enlaces(nit_entidad='899999102')
print(f"Con NIT específico - Nodos: {len(nodos)}, Enlaces: {len(enlaces)}")

# 3. Filtrar por departamento
nodos, enlaces = generar_nodos_y_enlaces(departamento='CUNDINAMARCA')
print(f"Por departamento - Nodos: {len(nodos)}, Enlaces: {len(enlaces)}")

# 4. Filtrar por rango de valores
nodos, enlaces = generar_nodos_y_enlaces(valor_minimo=1000000, valor_maximo=10000000)
print(f"Por rango de valores - Nodos: {len(nodos)}, Enlaces: {len(enlaces)}")

# 5. Filtrar por fechas
from datetime import datetime
nodos, enlaces = generar_nodos_y_enlaces(
    fecha_inicio=datetime(2023, 1, 1),
    fecha_fin=datetime(2023, 12, 31)
)
print(f"Por fechas - Nodos: {len(nodos)}, Enlaces: {len(enlaces)}")

# 6. Combinar múltiples filtros
nodos, enlaces = generar_nodos_y_enlaces(
    nit_entidad='860524654',
    valor_minimo=5000000,
    departamento='CUNDINAMARCA'
)
print(f"Múltiples filtros - Nodos: {len(nodos)}, Enlaces: {len(enlaces)}")

# 7. Filtrar por proveedor específico
nodos, enlaces = generar_nodos_y_enlaces(documento_proveedor='1067942322')
print(f"Por proveedor - Nodos: {len(nodos)}, Enlaces: {len(enlaces)}")

Sin filtros - Nodos: 13482, Enlaces: 12280
Con NIT específico - Nodos: 10, Enlaces: 9
Por departamento - Nodos: 0, Enlaces: 0
Por rango de valores - Nodos: 3941, Enlaces: 3120
Por fechas - Nodos: 2553, Enlaces: 1969
Múltiples filtros - Nodos: 0, Enlaces: 0
Por proveedor - Nodos: 2, Enlaces: 1


In [79]:
def generar_nodos_y_enlaces(nit_entidad=None, documento_proveedor=None, departamento=None, 
                            fecha_inicio=None, fecha_fin=None, valor_minimo=None, valor_maximo=None,
                            tamano_min=5, tamano_max=50):
    """
    Genera dos listas:
    1. nodos: Lista de diccionarios con entidades y proveedores
    2. enlaces: Lista de diccionarios con las relaciones entre entidades y proveedores
    
    Parámetros:
    - nit_entidad: Filtrar por un NIT de entidad específico
    - documento_proveedor: Filtrar por documento de proveedor específico
    - departamento: Filtrar por departamento
    - fecha_inicio: Filtrar contratos desde esta fecha
    - fecha_fin: Filtrar contratos hasta esta fecha
    - valor_minimo: Valor mínimo del contrato
    - valor_maximo: Valor máximo del contrato
    - tamano_min: Tamaño mínimo de los nodos (default: 5)
    - tamano_max: Tamaño máximo de los nodos (default: 50)
    """
    
    nodos = []
    enlaces = []
    enlaces_dict = {}
    
    # ============= CONSTRUIR QUERY BASE =============
    query_base = (db.contratos.id > 0)
    
    if nit_entidad:
        query_base &= (db.contratos.nit_entidad == nit_entidad)
    
    if documento_proveedor:
        query_base &= (db.contratos.documento_proveedor == documento_proveedor)
    
    if departamento:
        query_base &= (db.contratos.departamento == departamento)
    
    if fecha_inicio:
        query_base &= (db.contratos.fecha_inicio >= fecha_inicio)
    
    if fecha_fin:
        query_base &= (db.contratos.fecha_fin <= fecha_fin)
    
    if valor_minimo:
        query_base &= (db.contratos.valor_contrato >= valor_minimo)
    
    if valor_maximo:
        query_base &= (db.contratos.valor_contrato <= valor_maximo)
    
    # ============= PROCESAR ENTIDADES =============
    resultado = db.contratos.nit_entidad.count()
    suma_valor = db.contratos.valor_contrato.sum()
    
    query_entidades = query_base & (db.contratos.nit_entidad != None)
    
    conteos = db(query_entidades).select(
        db.contratos.nit_entidad,
        resultado,
        suma_valor,
        groupby=db.contratos.nit_entidad,
        having=resultado > 0,
        orderby=~resultado
    )
    
    # Lista temporal para almacenar nodos de entidades
    nodos_entidades = []
    
    for row in conteos:
        nitActual = row.contratos.nit_entidad
        valor_total = float(row[suma_valor] or 0)
        
        # Buscar datos de la entidad
        dataEntidad = db(db.entidades.nit_entidad == nitActual).select().last()
        
        try:
            nodo_entidad = {
                "id": nitActual,
                "name": dataEntidad.nombre_entidad,
                "departamento": dataEntidad.departamento,
                "tipo": "entidad",
                "url": "",
                "color": '#6da2c4',
                "size": 0,  # Se calculará después
                "cantidad_contratos": row[resultado],
                "valor_contrato": valor_total
            }
            nodos_entidades.append(nodo_entidad)
        except:
            # Si no existe en tabla entidades, usar datos del contrato
            dataContrato = db(db.contratos.nit_entidad == nitActual).select().first()
            if dataContrato:
                nodo_entidad = {
                    "id": nitActual,
                    "name": dataContrato.nombre_entidad or "Entidad Desconocida",
                    "departamento": dataContrato.departamento or "",
                    "tipo": "entidad",
                    "url": "",
                    "color": '#6da2c4',
                    "size": 0,  # Se calculará después
                    "cantidad_contratos": row[resultado],
                    "valor_contrato": valor_total
                }
                nodos_entidades.append(nodo_entidad)
    
    # ============= PROCESAR PROVEEDORES =============
    resultadoProv = db.contratos.documento_proveedor.count()
    suma_valor_prov = db.contratos.valor_contrato.sum()
    
    query_proveedores = query_base & (db.contratos.documento_proveedor != None)
    
    conteosProv = db(query_proveedores).select(
        db.contratos.documento_proveedor,
        resultadoProv,
        suma_valor_prov,
        groupby=db.contratos.documento_proveedor,
        having=resultadoProv > 0,
        orderby=~resultadoProv
    )
    
    # Lista temporal para almacenar nodos de proveedores
    nodos_proveedores = []
    
    for row in conteosProv:
        docActual = row.contratos.documento_proveedor
        valor_total = float(row[suma_valor_prov] or 0)
        
        # Buscar datos del proveedor
        dataProv = db(db.proveedoresypersonas.documento == docActual).select().last()
        
        try:
            nodo_proveedor = {
                "id": docActual,
                "name": dataProv.nombre,
                "es_pyme": dataProv.es_pyme or "No",
                "es_grupo": dataProv.es_grupo or "No",
                "tipo": "proveedor",
                "url": "",
                "color": "#1dc96a",
                "size": 0,  # Se calculará después
                "cantidad_contratos": row[resultadoProv],
                "valor_contrato": valor_total
            }
            nodos_proveedores.append(nodo_proveedor)
        except:
            # Si no existe en tabla proveedores, usar datos del contrato
            dataContrato = db(db.contratos.documento_proveedor == docActual).select().first()
            if dataContrato:
                nodo_proveedor = {
                    "id": docActual,
                    "name": dataContrato.proveedor_adjudicado or "Proveedor Desconocido",
                    "es_pyme": dataContrato.es_pyme or "No",
                    "es_grupo": dataContrato.es_grupo or "No",
                    "tipo": "proveedor",
                    "url": "",
                    "color": "#1dc96a",
                    "size": 0,  # Se calculará después
                    "cantidad_contratos": row[resultadoProv],
                    "valor_contrato": valor_total
                }
                nodos_proveedores.append(nodo_proveedor)
    
    # ============= NORMALIZAR TAMAÑOS =============
    # Combinar todos los nodos para calcular valores min y max globales
    todos_nodos = nodos_entidades + nodos_proveedores
    
    if len(todos_nodos) > 0:
        # Obtener valores mínimo y máximo de contratos
        valores = [nodo['valor_contrato'] for nodo in todos_nodos if nodo['valor_contrato'] > 0]
        
        if len(valores) > 0:
            valor_min_global = min(valores)
            valor_max_global = max(valores)
            
            # Evitar división por cero si todos los valores son iguales
            rango_valores = valor_max_global - valor_min_global
            
            if rango_valores > 0:
                # Normalización lineal: size = tamano_min + (valor - min) / (max - min) * (tamano_max - tamano_min)
                for nodo in todos_nodos:
                    if nodo['valor_contrato'] > 0:
                        valor_normalizado = (nodo['valor_contrato'] - valor_min_global) / rango_valores
                        nodo['size'] = tamano_min + valor_normalizado * (tamano_max - tamano_min)
                    else:
                        nodo['size'] = tamano_min
            else:
                # Si todos los valores son iguales, usar tamaño promedio
                tamano_promedio = (tamano_min + tamano_max) / 2
                for nodo in todos_nodos:
                    nodo['size'] = tamano_promedio
        else:
            # Si no hay valores, usar tamaño mínimo
            for nodo in todos_nodos:
                nodo['size'] = tamano_min
    
    # Agregar nodos normalizados a la lista final
    nodos = todos_nodos
    
    # ============= GENERAR ENLACES (RELACIONES) =============
    query_enlaces = query_base & (db.contratos.nit_entidad != None) & (db.contratos.documento_proveedor != None)
    
    contratos = db(query_enlaces).select(
        db.contratos.nit_entidad,
        db.contratos.documento_proveedor,
        db.contratos.valor_contrato
    )
    
    # Agrupar enlaces y sumar valores
    for contrato in contratos:
        source = contrato.nit_entidad
        target = contrato.documento_proveedor
        identificador = f"{source}_{target}"
        
        if identificador not in enlaces_dict:
            enlaces_dict[identificador] = {
                "source": source,
                "target": target,
                "identificador": identificador,
                "color": "#ff0000",
                "cantidad_contratos": 0,
                "valor_contrato": 0
            }
        
        enlaces_dict[identificador]["cantidad_contratos"] += 1
        enlaces_dict[identificador]["valor_contrato"] += float(contrato.valor_contrato or 0)
    
    # Convertir diccionario de enlaces a lista
    enlaces = list(enlaces_dict.values())
    
    return nodos, enlaces


# ============= EJEMPLOS DE USO =============


# 3. Tamaños más grandes para mejor visualización
nodos, enlaces = generar_nodos_y_enlaces(tamano_min=3, tamano_max=120)




# 6. Generar HTML con los datos


In [80]:
nodos

[{'id': '899999034',
  'name': 'SENA REGIONAL ANTIOQUIA Grupo Administrativo Complejo Itagüí',
  'departamento': 'Antioquia',
  'tipo': 'entidad',
  'url': '',
  'color': '#6da2c4',
  'size': 14.443716543455663,
  'cantidad_contratos': 750,
  'valor_contrato': 48514769785.0},
 {'id': '890399011',
  'name': 'SECRETARIA DE EDUCACION DE CALI',
  'departamento': 'Valle del Cauca',
  'tipo': 'entidad',
  'url': '',
  'color': '#6da2c4',
  'size': 15.06281827750565,
  'cantidad_contratos': 484,
  'valor_contrato': 51139404709.0},
 {'id': '899999061',
  'name': 'SECRETARÍA GENERAL DE LA ALCALDÍA MAYOR DE BOGOTÁ',
  'departamento': 'Distrito Capital de Bogotá',
  'tipo': 'entidad',
  'url': '',
  'color': '#6da2c4',
  'size': 11.91805140917555,
  'cantidad_contratos': 405,
  'valor_contrato': 37807403688.0},
 {'id': '8999990619',
  'name': '(Secretaría Distrital de Integración Social)',
  'departamento': 'Distrito Capital de Bogotá',
  'tipo': 'entidad',
  'url': '',
  'color': '#6da2c4',
  's

In [81]:
def generar_html_grafo(nodos, enlaces, titulo="Grafo de Contratos", nombre_archivo="grafo_contratos.html"):
    """
    Genera un archivo HTML con visualización de grafo D3.js a partir de nodos y enlaces
    
    Parámetros:
    - nodos: Lista de diccionarios con nodos (entidades y proveedores)
    - enlaces: Lista de diccionarios con enlaces entre nodos
    - titulo: Título del grafo
    - nombre_archivo: Nombre del archivo HTML a generar
    """
    
    # Convertir nodos a formato JavaScript
    nodos_js = "[\n"
    for i, nodo in enumerate(nodos):
        nname=nodo['name'].replace("'","")
        coma = "," if i < len(nodos) - 1 else ""
        nodos_js += f"    {{ id: '{nodo['id']}', name: '{nname}', "
        
        # Agregar campos según el tipo de nodo
        if nodo['tipo'] == 'entidad':
            nodos_js += f"dep: '{nodo.get('departamento', '')}', "
        else:  # proveedor
            nodos_js += f"es_pyme: '{nodo.get('es_pyme', 'No')}', es_grupo: '{nodo.get('es_grupo', 'No')}', "
        
        nodos_js += f"url: '{nodo.get('url', '')}', color: '{nodo['color']}', "
        nodos_js += f"cantidad_contratos: {nodo['cantidad_contratos']}, size: {nodo['size']}, valor: {nodo['valor_contrato']}, tipo: '{nodo['tipo']}'}}{coma}\n"
    nodos_js += "]"
    
    # Convertir enlaces a formato JavaScript
    enlaces_js = "[\n"
    for i, enlace in enumerate(enlaces):
        coma = "," if i < len(enlaces) - 1 else ""
        enlaces_js += f"    {{ source: '{enlace['source']}', target: '{enlace['target']}', "
        enlaces_js += f"identificador: '{enlace['identificador']}', color: '{enlace['color']}', "
        enlaces_js += f"cantidad_contratos: {enlace['cantidad_contratos']}, "
        enlaces_js += f"valor_contrato: {enlace['valor_contrato']}}}{coma}\n"
    enlaces_js += "]"
    
    # Generar items de leyenda para entidades
    leyenda_entidades = ""
    entidades_unicas = {}
    for nodo in nodos:
        if nodo['tipo'] == 'entidad':
            dep = nodo.get('departamento', 'Sin departamento')
            if dep not in entidades_unicas:
                entidades_unicas[dep] = nodo['color']
    
    for dep, color in list(entidades_unicas.items())[:10]:  # Limitar a 10 para no saturar
        leyenda_entidades += f"""
            <div class="legend-item">
                <div class="legend-color" style="background: {color};"></div>
                <span>{dep}</span>
            </div>"""
    
    # Template HTML
    html_content = f"""<!DOCTYPE html>
<html lang="es">
<head>
    <meta charset="UTF-8">
    <meta name="viewport" content="width=device-width, initial-scale=1.0">
    <title>Grafo de Contratos</title>
    <script src="https://cdnjs.cloudflare.com/ajax/libs/d3/7.8.5/d3.min.js"></script>
    <style>
        body {{
            margin: 0;
            padding: 20px;
            font-family: Arial, sans-serif;
            background: #f5f5f5;
            align-items: center;
            justify-content: center;
        }}
        #graph {{
            background: white;
            border-radius: 8px;
            box-shadow: 0 2px 8px rgba(0,0,0,0.1);
            width: 97%;
            height: 97%;
        }}
        .node {{
            cursor: pointer;
            transition: r 0.2s;
        }}
        .node:hover {{
            stroke: #333;
            stroke-width: 3px;
        }}
        .node-label {{
            font-size: 12px;
            pointer-events: none;
            user-select: none;
            fill: #333;
            font-weight: 500;
        }}
        .link {{
            stroke-opacity: 0.6;
        }}
        .link:hover {{
            stroke: #2cf105;
            stroke-width: 3px;
        }}
        .tooltip {{
            position: absolute;
            padding: 8px 12px;
            background: rgba(0, 0, 0, 0.8);
            color: white;
            border-radius: 4px;
            font-size: 12px;
            pointer-events: none;
            opacity: 0;
            transition: opacity 0.2s;
            z-index: 1000;
        }}
        .infodiv {{
            width: 100%;
            align-items: center;
            justify-content: center;
            display: flex;
            flex-wrap: wrap;
        }}
        #title {{
            width: 100%;
            height: 30px;
            background: gray;
            color: white;
            border-radius: 8px;
            box-shadow: 0 2px 8px rgba(0,0,0,0.1);
            align-items: center;
            justify-content: center;
            display: flex;
        }}
        .legend {{
            position: fixed;
            top: 80px;
            right: 20px;
            background: white;
            padding: 20px;
            border-radius: 8px;
            box-shadow: 0 4px 12px rgba(0,0,0,0.15);
            max-width: 300px;
            max-height: 80vh;
            overflow-y: auto;
            z-index: 999;
            transition: transform 0.3s ease;
        }}
        .legend.hidden {{
            transform: translateX(350px);
        }}
        .legend h3 {{
            margin-top: 0;
            margin-bottom: 15px;
            font-size: 16px;
            color: #333;
            border-bottom: 2px solid #eee;
            padding-bottom: 8px;
        }}
        .legend-section {{
            margin-bottom: 20px;
        }}
        .legend-section h4 {{
            margin: 0 0 10px 0;
            font-size: 14px;
            color: #666;
        }}
        .legend-item {{
            display: flex;
            align-items: center;
            margin-bottom: 8px;
            font-size: 12px;
        }}
        .legend-color {{
            width: 20px;
            height: 20px;
            border-radius: 50%;
            margin-right: 10px;
            border: 2px solid #fff;
            box-shadow: 0 1px 3px rgba(0,0,0,0.2);
        }}
        .legend-line {{
            width: 30px;
            height: 3px;
            margin-right: 10px;
        }}
        .toggle-legend-btn {{
            position: fixed;
            top: 30px;
            right: 20px;
            background: #4CAF50;
            color: white;
            border: none;
            padding: 10px 20px;
            border-radius: 5px;
            cursor: pointer;
            font-size: 14px;
            box-shadow: 0 2px 8px rgba(0,0,0,0.2);
            z-index: 1000;
            transition: background 0.3s;
        }}
        .toggle-legend-btn:hover {{
            background: #45a049;
        }}
    </style>
</head>
<body>
    <button class="toggle-legend-btn" onclick="toggleLegend()">Mostrar/Ocultar Leyenda</button>

    <div class="infodiv">
        <div id="title" class="title">
            <p style="margin: 0px">{titulo}</p>
        </div>
        <div id="tooltip" class="tooltip"></div>
        <svg id="graph"></svg>
        
        <div id="legend" class="legend">
            <h3>Leyenda del Grafo</h3>

            <div class="legend-section">
                <h4>Nodos - Entidades</h4>
                <div class="legend-item">
                    <div class="legend-color" style="background: #6da2c4;"></div>
                    <span>Entidades (azul)</span>
                </div>
            </div>

            <div class="legend-section">
                <h4>Nodos - Proveedores</h4>
                <div class="legend-item">
                    <div class="legend-color" style="background: #1dc96a;"></div>
                    <span>Proveedores (verde)</span>
                </div>
            </div>

            <div class="legend-section">
                <h4>Enlaces (Contratos)</h4>
                <div class="legend-item">
                    <div class="legend-line" style="background: #ff0000;"></div>
                    <span>Relación contractual</span>
                </div>
            </div>

            <div class="legend-section">
                <h4>Tamaño de nodos</h4>
                <div class="legend-item">
                    <span>Representa el número de contratos</span>
                </div>
            </div>

            <div class="legend-section">
                <h4>Estadísticas</h4>
                <div class="legend-item">
                    <span>Total nodos: {len(nodos)}</span>
                </div>
                <div class="legend-item">
                    <span>Total enlaces: {len(enlaces)}</span>
                </div>
                <div class="legend-item">
                    <span>Entidades: {len([n for n in nodos if n['tipo'] == 'entidad'])}</span>
                </div>
                <div class="legend-item">
                    <span>Proveedores: {len([n for n in nodos if n['tipo'] == 'proveedor'])}</span>
                </div>
            </div>
        </div>
    </div>

    <script>
        const nodes = {nodos_js};
        
        const links = {enlaces_js};

        function toggleLegend() {{
            const legend = document.getElementById('legend');
            legend.classList.toggle('hidden');
        }}

        function formatNumber(num) {{
            return new Intl.NumberFormat('es-CO', {{ 
                style: 'currency', 
                currency: 'COP',
                minimumFractionDigits: 0,
                maximumFractionDigits: 0
            }}).format(num);
        }}

        // Configuración del SVG
        const width = window.innerWidth - 40;
        const height = window.innerHeight - 40;

        const svg = d3.select('#graph')
            .attr('width', width)
            .attr('height', height);

        const tooltip = d3.select('#tooltip');

        // Contenedor para zoom
        const g = svg.append('g');

        // Zoom
        const zoom = d3.zoom()
            .scaleExtent([0.1, 10])
            .on('zoom', (event) => {{
                g.attr('transform', event.transform);
            }});

        svg.call(zoom);
        svg.call(zoom.transform, d3.zoomIdentity
            .translate(width / 2, height / 2)
            .scale(0.5)
            .translate(-width / 2, -height / 2)
        );

        // Simulación de fuerzas
        const simulation = d3.forceSimulation(nodes)
            .force('link', d3.forceLink(links).id(d => d.id).distance(50))
            .force('charge', d3.forceManyBody().strength(-2))
            .force('center', d3.forceCenter(width / 2, height / 2))
            .force('collision', d3.forceCollide().radius(d => d.size +5 ));

        // Crear enlaces
        const link = g.append('g')
            .selectAll('line')
            .data(links)
            .join('line')
            .attr('class', 'link')
            .attr('stroke', d => d.color)
            .attr('stroke-width', d => Math.max(2, Math.min(10, d.cantidad_contratos / 2)))
            .on('mouseover', (event, d) => {{
                tooltip
                    .style('opacity', 1)
                    .html(`
                        <strong>Relación Contractual</strong><br>
                        Entidad: ${{nodes.find(n => n.id === d.source.id).name}}<br>
                        Proveedor: ${{nodes.find(n => n.id === d.target.id).name}}<br>
                        Contratos: ${{d.cantidad_contratos}}<br>
                        Valor total: ${{formatNumber(d.valor_contrato)}}
                    `)
                    .style('left', (event.pageX + 10) + 'px')
                    .style('top', (event.pageY - 10) + 'px');
                
                node
                    .filter(n => n.id === d.source.id || n.id === d.target.id)
                    .attr('stroke', '#2cf105')
                    .attr('stroke-width', 3);
            }})
            .on('mouseout', () => {{
                tooltip.style('opacity', 0);
                node
                    .attr('stroke', '#fff')
                    .attr('stroke-width', 2);
            }});

        // Crear nodos
        const node = g.append('g')
            .selectAll('circle')
            .data(nodes)
            .join('circle')
            .attr('class', 'node')
            .attr('r', d => Math.max(5, Math.min(50, d.size)))
            .attr('fill', d => d.color)
            .attr('stroke', '#fff')
            .attr('stroke-width', 2)
            .call(drag(simulation))
            .on('mouseover', (event, d) => {{
                let tooltipContent = `<strong>${{d.name}}</strong><br>`;
                tooltipContent += `Tipo: ${{d.tipo === 'entidad' ? 'Entidad' : 'Proveedor'}}<br>`;
                tooltipContent += `ID: ${{d.id}}<br>`;
                
                if (d.tipo === 'entidad') {{
                    tooltipContent += `Departamento: ${{d.dep || 'N/A'}}<br>`;
                }} else {{
                    tooltipContent += `PyME: ${{d.es_pyme}}<br>`;
                    tooltipContent += `Grupo: ${{d.es_grupo}}<br>`;
                }}
                
                tooltipContent += `Contratos: ${{d.cantidad_contratos}}<br>`;
                tooltipContent += `Valor total: ${{formatNumber(d.valor)}}`;
                
                tooltip
                    .style('opacity', 1)
                    .html(tooltipContent)
                    .style('left', (event.pageX + 10) + 'px')
                    .style('top', (event.pageY - 10) + 'px');
            }})
            .on('mouseout', () => {{
                tooltip.style('opacity', 0);
            }});

        // Etiquetas de nodos
        const label = g.append('g')
            .selectAll('text')
            .data(nodes)
            .join('text')
            .attr('class', 'node-label')
            .attr('text-anchor', 'middle')
            .attr('dy', d => -(Math.max(5, Math.min(50, d.size)) + 5));
            //.text(d => d.name.length > 30 ? d.name.substring(0, 30) + '...' : d.name);

        // Actualizar posiciones en cada tick
        simulation.on('tick', () => {{
            link
                .attr('x1', d => d.source.x)
                .attr('y1', d => d.source.y)
                .attr('x2', d => d.target.x)
                .attr('y2', d => d.target.y);

            node
                .attr('cx', d => d.x)
                .attr('cy', d => d.y);

            label
                .attr('x', d => d.x)
                .attr('y', d => d.y);
        }});

        // Función de arrastre
        function drag(simulation) {{
            function dragstarted(event) {{
                if (!event.active) simulation.alphaTarget(0.3).restart();
                event.subject.fx = event.subject.x;
                event.subject.fy = event.subject.y;
            }}

            function dragged(event) {{
                event.subject.fx = event.x;
                event.subject.fy = event.y;
            }}

            function dragended(event) {{
                if (!event.active) simulation.alphaTarget(0);
                event.subject.fx = null;
                event.subject.fy = null;
            }}

            return d3.drag()
                .on('start', dragstarted)
                .on('drag', dragged)
                .on('end', dragended);
        }}

        // Ajustar tamaño al cambiar ventana
        window.addEventListener('resize', () => {{
            const newWidth = window.innerWidth - 40;
            const newHeight = window.innerHeight - 40;
            svg.attr('width', newWidth).attr('height', newHeight);
            simulation.force('center', d3.forceCenter(newWidth / 2, newHeight / 2));
            simulation.alpha(0.3).restart();
        }});
    </script>
</body>
</html>"""

    # Guardar archivo
    with open(nombre_archivo, 'w', encoding='utf-8') as f:
        f.write(html_content)
    
    print(f"Archivo HTML generado: {nombre_archivo}")
    return nombre_archivo


# ============= EJEMPLO DE USO COMPLETO =============

generar_html_grafo(
    nodos=nodos,
    enlaces=enlaces,
    titulo="Red de Contratos con Tamaños Normalizados",
    nombre_archivo="grafo_normalizado.html"
)

Archivo HTML generado: grafo_normalizado.html


'grafo_normalizado.html'

In [34]:
nodos

[{'id': '899999034',
  'name': 'SENA REGIONAL ANTIOQUIA Grupo Administrativo Complejo Itagüí',
  'departamento': 'Antioquia',
  'tipo': 'entidad',
  'url': '',
  'color': '#6da2c4',
  'size': 750,
  'valor_contrato': 48514769785.0},
 {'id': '890399011',
  'name': 'SECRETARIA DE EDUCACION DE CALI',
  'departamento': 'Valle del Cauca',
  'tipo': 'entidad',
  'url': '',
  'color': '#6da2c4',
  'size': 484,
  'valor_contrato': 51139404709.0},
 {'id': '899999061',
  'name': 'SECRETARÍA GENERAL DE LA ALCALDÍA MAYOR DE BOGOTÁ',
  'departamento': 'Distrito Capital de Bogotá',
  'tipo': 'entidad',
  'url': '',
  'color': '#6da2c4',
  'size': 405,
  'valor_contrato': 37807403688.0},
 {'id': '8999990619',
  'name': '(Secretaría Distrital de Integración Social)',
  'departamento': 'Distrito Capital de Bogotá',
  'tipo': 'entidad',
  'url': '',
  'color': '#6da2c4',
  'size': 351,
  'valor_contrato': 78358867090.0},
 {'id': '899999239',
  'name': 'ICBF REGIONAL BOGOTA',
  'departamento': 'Distrito 

In [14]:
import polars as pl
import numpy as np

# Supongamos que tu DataFrame se llama 'df'
df = ContratosClean2
print("="*80)
print("1. ESTRUCTURA Y CALIDAD DE DATOS")
print("="*80)

# Dimensiones del dataset
print(f"\n📊 Dimensiones del Dataset:")
print(f"   Filas: {df.height:,}")
print(f"   Columnas: {df.width}")

# Información de tipos de datos
print(f"\n📋 Tipos de Datos:")
print(df.schema)

# Análisis de valores nulos
print(f"\n❌ Análisis de Valores Nulos:")
nulos = df.null_count()
nulos_pct = (df.null_count() / df.height * 100).transpose(
    include_header=True,
    header_name="columna",
    column_names=["porcentaje_nulo"]
)

# Combinar conteos y porcentajes
analisis_nulos = pl.DataFrame({
    'columna': df.columns,
    'valores_nulos': nulos.row(0),
    'porcentaje_nulo': nulos_pct['porcentaje_nulo'].to_list()
}).sort('porcentaje_nulo', descending=True)

print(analisis_nulos.filter(pl.col('porcentaje_nulo') > 0))

# Columnas con más del 50% de nulos (críticas)
criticas = analisis_nulos.filter(pl.col('porcentaje_nulo') > 50)
if criticas.height > 0:
    print(f"\n⚠️  Columnas con más del 50% de valores nulos:")
    print(criticas)

# Verificar duplicados en IdContrato
duplicados = df.group_by('IdContrato').agg(
    pl.len().alias('conteo')
).filter(pl.col('conteo') > 1)

print(f"\n🔍 Duplicados en IdContrato:")
print(f"   Contratos duplicados: {duplicados.height}")
if duplicados.height > 0:
    print(f"   Ejemplo de duplicados:")
    print(duplicados.head())

# Resumen de completitud por columna
print(f"\n✅ Completitud General:")
completitud = (df.null_count() / df.height * 100).transpose(
    include_header=True,
    header_name="columna",
    column_names=["completitud"]
).sort('completitud')

print(f"   Columnas 100% completas: {completitud.filter(pl.col('completitud') == 100).height}")
print(f"   Columnas con datos: {completitud.filter(pl.col('completitud') > 0).height}")
print(f"   Columnas vacías: {completitud.filter(pl.col('completitud') == 0).height}")

1. ESTRUCTURA Y CALIDAD DE DATOS

📊 Dimensiones del Dataset:
   Filas: 500
   Columnas: 70

📋 Tipos de Datos:
Schema([('IdContrato', String), ('RefContrato', String), ('EstadoContrato', String), ('CodigoDeCategoriaPrincipal', String), ('TipodeContrato', String), ('ModalidadDeContratacion', String), ('JustificacionModalidadContratacion', String), ('ObjetoDelContrato', String), ('URLProceso', String), ('DuracióndelContrato', String), ('ElContratoPuedeSerProrrogado', String), ('FechaDeNotificaciónDeProrrogación', Date), ('FechaDeFirma', Date), ('FechaDeInicioContrato', Date), ('FechaDeFinContrato', Date), ('DiasAdicionados', Int64), ('FechaInicioLiquidacion', Date), ('FechaFinLiquidacion', Date), ('NombreEntidad', String), ('NitEntidad', Int64), ('EntidadCentralizada', String), ('CodigoProveedor', Int64), ('DocumentoProveedor', Int64), ('ProveedorAdjudicado', String), ('EsGrupo', String), ('EsPyme', String), ('NacionalidadRepresentanteLegal', String), ('DomicilioRepresentanteLegal', Strin

In [ ]:
contratos_duplicados = df.group_by('IdContrato').agg([
        pl.len().alias('num_registros')
    ]).filter(pl.col('num_registros') > 1).sort('num_registros', descending=True)
    
total_duplicados = contratos_duplicados.height


In [8]:
import polars as pl
import pandas as pd

def analizar_contratos_duplicados(df, campo_contrato='IdContrato'):
    """
    Analiza contratos duplicados y muestra qué columnas son diferentes
    
    Args:
        df: DataFrame de Polars
        campo_contrato: Nombre de la columna que identifica el contrato (default: 'IdContrato')
    
    Returns:
        DataFrame con el análisis de duplicados
    """
    
    print("="*80)
    print(f"ANÁLISIS DE CONTRATOS DUPLICADOS")
    print("="*80)
    height= df.height
    # Encontrar contratos que aparecen más de una vez
    contratos_duplicados = df.group_by('IdContrato').agg([
        pl.len().alias('num_registros')
    ]).filter(pl.col('num_registros') > 1).sort('num_registros', descending=True)
    
    total_duplicados = contratos_duplicados.height
    
    print(f"\n📊 RESUMEN GENERAL:")
    print(f"   Total de contratos únicos: {df[campo_contrato].n_unique():,}")
    print(f"   Contratos con registros duplicados: {total_duplicados:,}")
    print(f"   Total de registros duplicados: {df.filter(pl.col('IdContrato').is_in(contratos_duplicados['IdContrato'].implode())).height}")
    
    if total_duplicados == 0:
        print("\n✓ No se encontraron contratos duplicados")
        return None
    
    print(f"\n🔍 Top 10 Contratos con Más Duplicados:")
    print(contratos_duplicados.head(10))
    
    return contratos_duplicados


def comparar_duplicados_contrato(df, id_contrato, campo_contrato='IdContrato'):
    """
    Compara todas las filas de un contrato duplicado y muestra las diferencias
    
    Args:
        df: DataFrame de Polars
        id_contrato: ID del contrato a analizar
        campo_contrato: Nombre de la columna que identifica el contrato
    """
    
    # Filtrar todas las filas del contrato
    filas_contrato = df.filter(pl.col(campo_contrato) == id_contrato)
    num_filas = filas_contrato.height
    
    if num_filas == 0:
        print(f"❌ No se encontró el contrato: {id_contrato}")
        return None
    
    if num_filas == 1:
        print(f"ℹ️  El contrato {id_contrato} no está duplicado (solo 1 registro)")
        return None
    
    print("="*80)
    print(f"ANÁLISIS DE DUPLICADOS PARA CONTRATO: {id_contrato}")
    print(f"Número de registros encontrados: {num_filas}")
    print("="*80)
    
    # Analizar columna por columna
    resultados = []
    columnas_diferentes = []
    columnas_iguales = []
    
    for columna in df.columns:
        valores = filas_contrato[columna].to_list()
        valores_unicos = filas_contrato[columna].n_unique()
        
        # Determinar si todos los valores son iguales
        if valores_unicos == 1:
            # Todos iguales (incluyendo si todos son null)
            columnas_iguales.append(columna)
            estado = "✓ Iguales"
            valor_ejemplo = str(valores[0])[:50]
        else:
            # Hay diferencias
            columnas_diferentes.append(columna)
            estado = "✗ Diferentes"
            valor_ejemplo = f"{valores_unicos} valores distintos"
        
        resultados.append({
            'Columna': columna,
            'Estado': estado,
            'Valores_Unicos': valores_unicos,
            'Valores': valores
        })
    
    # Crear DataFrame de resultados
    df_analisis = pl.DataFrame({
        'Columna': [r['Columna'] for r in resultados],
        'Estado': [r['Estado'] for r in resultados],
        'Valores_Unicos': [r['Valores_Unicos'] for r in resultados]
    })
    
    # Resumen
    print(f"\n📊 RESUMEN:")
    print(f"   Total de columnas: {len(df.columns)}")
    print(f"   Columnas iguales en todos los registros: {len(columnas_iguales)} ({len(columnas_iguales)/len(df.columns)*100:.1f}%)")
    print(f"   Columnas diferentes: {len(columnas_diferentes)} ({len(columnas_diferentes)/len(df.columns)*100:.1f}%)")
    
    if len(columnas_diferentes) == 0:
        print(f"\n✓ TODOS LOS REGISTROS SON EXACTAMENTE IGUALES (Duplicados perfectos)")
    else:
        print(f"\n⚠️  LOS REGISTROS TIENEN DIFERENCIAS EN {len(columnas_diferentes)} COLUMNAS")
    
    # Mostrar solo las columnas diferentes con detalle
    if len(columnas_diferentes) > 0:
        print(f"\n🔍 COLUMNAS CON DIFERENCIAS:")
        print("-" * 80)
        
        for columna in columnas_diferentes:
            valores = filas_contrato[columna].to_list()
            print(f"\n📌 {columna}:")
            for i, valor in enumerate(valores):
                print(f"   Registro {i+1}: {valor}")
    
    # Mostrar tabla comparativa lado a lado
    print(f"\n📋 TABLA COMPARATIVA (Todas las columnas):")
    print("-" * 80)
    
    # Transponer para mostrar columnas como filas
    filas_dict = {}
    for i in range(num_filas):
        filas_dict[f'Registro_{i+1}'] = filas_contrato.row(i)
    
    # Crear DataFrame comparativo (convertir todo a string para evitar errores de tipo)
    comparacion_dict = {'Columna': df.columns}
    
    for i in range(num_filas):
        comparacion_dict[f'Registro_{i+1}'] = [
            str(filas_contrato[col][i]) for col in df.columns
        ]
    
    comparacion = pl.DataFrame(comparacion_dict)
    
    print(comparacion)
    
    return df_analisis, comparacion


def analizar_todos_duplicados(df, campo_contrato='IdContrato', max_contratos=10):
    """
    Analiza todos los contratos duplicados y genera un reporte
    
    Args:
        df: DataFrame de Polars
        campo_contrato: Nombre de la columna que identifica el contrato
        max_contratos: Máximo número de contratos a analizar en detalle
    """
    
    print("="*80)
    print(f"ANÁLISIS COMPLETO DE TODOS LOS DUPLICADOS")
    print("="*80)
    
    # Encontrar todos los contratos duplicados
    contratos_duplicados = df.group_by(campo_contrato).agg([
        pl.len().alias('num_registros')
    ]).filter(pl.col('num_registros') > 1).sort('num_registros', descending=True)
    
    if contratos_duplicados.height == 0:
        print("\n✓ No hay contratos duplicados")
        return None
    
    print(f"\nAnalizando {min(max_contratos, contratos_duplicados.height)} contratos duplicados...")
    
    # Resumen de análisis
    resumen_general = []
    
    for i in range(min(max_contratos, contratos_duplicados.height)):
        id_contrato = contratos_duplicados[campo_contrato][i]
        num_registros = contratos_duplicados['num_registros'][i]
        
        # Obtener filas del contrato
        filas_contrato = df.filter(pl.col(campo_contrato) == id_contrato)
        
        # Contar columnas diferentes
        columnas_diferentes = 0
        for columna in df.columns:
            if filas_contrato[columna].n_unique() > 1:
                columnas_diferentes += 1
        
        son_identicos = (columnas_diferentes == 0)
        
        resumen_general.append({
            'Contrato': id_contrato,
            'Num_Registros': num_registros,
            'Columnas_Diferentes': columnas_diferentes,
            'Son_Identicos': '✓ SÍ' if son_identicos else '✗ NO'
        })
    
    # Mostrar resumen
    df_resumen = pl.DataFrame(resumen_general)
    print(f"\n📊 RESUMEN DE DUPLICADOS:")
    print(df_resumen)
    
    # Estadísticas
    identicos = sum(1 for r in resumen_general if r['Columnas_Diferentes'] == 0)
    diferentes = len(resumen_general) - identicos
    
    print(f"\n📈 ESTADÍSTICAS:")
    print(f"   Duplicados exactos (registros idénticos): {identicos}")
    print(f"   Duplicados con diferencias: {diferentes}")
    
    return df_resumen


# =============================================================================
# EJEMPLOS DE USO
# =============================================================================

print("\n" + "="*80)
print("PASO 1: Identificar contratos duplicados")
print("="*80)

# Identificar todos los contratos duplicados
duplicados = analizar_contratos_duplicados(df)


print("\n" + "="*80)
print("PASO 2: Analizar un contrato duplicado específico")
print("="*80)

# Si hay duplicados, analiza el primero como ejemplo
for i in range(len(duplicados)):
    primer_duplicado = duplicados['IdContrato'][i]
    print(f"\nAnalizando el contrato: {primer_duplicado}")
    analisis, comparacion = comparar_duplicados_contrato(df, primer_duplicado)
    
    # Para analizar otro contrato específico:
    # comparar_duplicados_contrato(df, 'TU_ID_CONTRATO_AQUI')


# print("\n" + "="*80)
# print("PASO 3: Análisis completo de todos los duplicados")
# print("="*80)

# # Analizar todos los duplicados (o los primeros 10)
# resumen_completo = analizar_todos_duplicados(df, max_contratos=100)


# =============================================================================
# FUNCIONES ADICIONALES ÚTILES
# =============================================================================

def exportar_duplicados(df, archivo_salida='duplicados_analisis.csv', campo_contrato='IdContrato'):
    """
    Exporta todos los contratos duplicados a un archivo CSV para análisis manual
    """
    contratos_duplicados = df.group_by(campo_contrato).agg([
        pl.len().alias('num_registros')
    ]).filter(pl.col('num_registros') > 1)
    
    # Filtrar el DataFrame original solo con los duplicados
    df_duplicados = df.filter(pl.col(campo_contrato).is_in(contratos_duplicados[campo_contrato]))
    df_duplicados = df_duplicados.sort(campo_contrato)
    
    # Exportar
    df_duplicados.write_csv(archivo_salida)
    print(f"\n💾 Duplicados exportados a: {archivo_salida}")
    print(f"   Total de registros exportados: {df_duplicados.height:,}")
    
    return df_duplicados



PASO 1: Identificar contratos duplicados
ANÁLISIS DE CONTRATOS DUPLICADOS

📊 RESUMEN GENERAL:
   Total de contratos únicos: 481
   Contratos con registros duplicados: 19
   Total de registros duplicados: 38

🔍 Top 10 Contratos con Más Duplicados:
shape: (10, 2)
┌────────────────────┬───────────────┐
│ IdContrato         ┆ num_registros │
│ ---                ┆ ---           │
│ str                ┆ u32           │
╞════════════════════╪═══════════════╡
│ CO1.PCCNTR.1002740 ┆ 2             │
│ CO1.PCCNTR.1002725 ┆ 2             │
│ CO1.PCCNTR.1001106 ┆ 2             │
│ CO1.PCCNTR.1001044 ┆ 2             │
│ CO1.PCCNTR.1002713 ┆ 2             │
│ CO1.PCCNTR.1003012 ┆ 2             │
│ CO1.PCCNTR.1002919 ┆ 2             │
│ CO1.PCCNTR.1002925 ┆ 2             │
│ CO1.PCCNTR.1003044 ┆ 2             │
│ CO1.PCCNTR.1002931 ┆ 2             │
└────────────────────┴───────────────┘

PASO 2: Analizar un contrato duplicado específico

Analizando el contrato: CO1.PCCNTR.1002740
ANÁLISIS DE DUPLIC

In [ ]:

import polars as pl
import numpy as np
import json

# Supongamos que tu DataFrame se llama 'df'
df = ContratosClean2
def get_info_df(df: pl.DataFrame,name_df="",seccion="") -> dict:
    """
    Genera un informe detallado sobre la estructura y calidad de datos de un DataFrame de Polars.
    
    Args:
        df: DataFrame de Polars a analizar.
    
    Returns:
        Diccionario con el informe estructurado.
    """
    # Diccionario para almacenar todos los resultados
    resultados = {}

    # ============================================================================
    # 1. ESTRUCTURA Y CALIDAD DE DATOS
    # ============================================================================

    # Dimensiones del dataset
    resultados['dimensiones'] = {
        'filas': df.height,
        'columnas': df.width
    }

    # Información de tipos de datos
    resultados['tipos_datos'] = {col: str(dtype) for col, dtype in df.schema.items()}

    # Análisis de valores nulos
    nulos = df.null_count()
    nulos_pct = (df.null_count() / df.height * 100).transpose(
        include_header=True,
        header_name="columna",
        column_names=["porcentaje_nulo"]
    )

    # Combinar conteos y porcentajes
    analisis_nulos = pl.DataFrame({
        'columna': df.columns,
        'valores_nulos': nulos.row(0),
        'porcentaje_nulo': nulos_pct['porcentaje_nulo'].to_list()
    }).sort('porcentaje_nulo', descending=True)

    # Convertir análisis de nulos a dict
    resultados['analisis_nulos'] = {
        'detalle': analisis_nulos.filter(pl.col('porcentaje_nulo') > 0).to_dicts(),
        'total_columnas_con_nulos': analisis_nulos.filter(pl.col('porcentaje_nulo') > 0).height
    }

    # Columnas con más del 50% de nulos (críticas)
    criticas = analisis_nulos.filter(pl.col('porcentaje_nulo') > 50)
    resultados['columnas_criticas'] = {
        'cantidad': criticas.height,
        'detalle': criticas.to_dicts() if criticas.height > 0 else []
    }

    # Verificar duplicados en IdContrato
    duplicados = df.group_by('IdContrato').agg(
        pl.len().alias('conteo')
    ).filter(pl.col('conteo') > 1)

    resultados['duplicados_idcontrato'] = {
        'cantidad': duplicados.height,
        'ejemplos': duplicados.head().to_dicts() if duplicados.height > 0 else []
    }

    # Resumen de completitud por columna
    completitud =(( df.null_count() / df.height) * -100)+100
    completitud_df = pl.DataFrame({
        'columna': df.columns,
        'completitud': completitud.row(0)
    }).sort('completitud')

    resultados['completitud_general'] = {
        'columnas_100_completas': completitud_df.filter(pl.col('completitud') == 100).height,
        'columnas_con_datos': completitud_df.filter(pl.col('completitud') > 0).height,
        'columnas_vacias': completitud_df.filter(pl.col('completitud') == 0).height,
        'detalle_por_columna': completitud_df.to_dicts()
    }

    cargar_estadistica("contratos", "All", "All", str(resultados["dimensiones"]["filas"]), texto_visible="Contratos en bases de datos")
    cargar_estadistica("contratos_vars", "All", "All", str(resultados["dimensiones"]["columnas"]), texto_visible="Variables en bases de datos")
    cargar_estadistica("contratos_nulls", "All", "All", str(resultados["analisis_nulos"]['total_columnas_con_nulos']), texto_visible="Columnas con valores nulos")
    cargar_estadistica("contratos_critica", "All", "All", str(resultados["columnas_criticas"]["cantidad"]), texto_visible="Columnas con mas de 50% en valores nulos")
    cargar_estadistica("contratos", "All", "All", str(resultados["duplicados_idcontrato"]["cantidad"]), texto_visible="Contratos con IDs duplicados duplicados")


    # Imprimir resultado en formato JSON
    
    return resultados
get_info_df(df)

{"message":"Estadística actualizada","id":4,"accion":"actualizar"}
{"message":"Estadística actualizada","id":4,"accion":"actualizar"}
{"message":"Estadística actualizada","id":4,"accion":"actualizar"}
{"message":"Estadística actualizada","id":4,"accion":"actualizar"}
{"message":"Estadística actualizada","id":4,"accion":"actualizar"}


{'dimensiones': {'filas': 500, 'columnas': 70},
 'tipos_datos': {'IdContrato': 'String',
  'RefContrato': 'String',
  'EstadoContrato': 'String',
  'CodigoDeCategoriaPrincipal': 'String',
  'TipodeContrato': 'String',
  'ModalidadDeContratacion': 'String',
  'JustificacionModalidadContratacion': 'String',
  'ObjetoDelContrato': 'String',
  'URLProceso': 'String',
  'DuracióndelContrato': 'String',
  'ElContratoPuedeSerProrrogado': 'String',
  'FechaDeNotificaciónDeProrrogación': 'Date',
  'FechaDeFirma': 'Date',
  'FechaDeInicioContrato': 'Date',
  'FechaDeFinContrato': 'Date',
  'DiasAdicionados': 'Int64',
  'FechaInicioLiquidacion': 'Date',
  'FechaFinLiquidacion': 'Date',
  'NombreEntidad': 'String',
  'NitEntidad': 'Int64',
  'EntidadCentralizada': 'String',
  'CodigoProveedor': 'Int64',
  'DocumentoProveedor': 'Int64',
  'ProveedorAdjudicado': 'String',
  'EsGrupo': 'String',
  'EsPyme': 'String',
  'NacionalidadRepresentanteLegal': 'String',
  'DomicilioRepresentanteLegal': 'Stri

28

In [36]:
resultados

{'dimensiones': {'filas': 500, 'columnas': 70},
 'tipos_datos': {'IdContrato': 'String',
  'RefContrato': 'String',
  'EstadoContrato': 'String',
  'CodigoDeCategoriaPrincipal': 'String',
  'TipodeContrato': 'String',
  'ModalidadDeContratacion': 'String',
  'JustificacionModalidadContratacion': 'String',
  'ObjetoDelContrato': 'String',
  'URLProceso': 'String',
  'DuracióndelContrato': 'String',
  'ElContratoPuedeSerProrrogado': 'String',
  'FechaDeNotificaciónDeProrrogación': 'Date',
  'FechaDeFirma': 'Date',
  'FechaDeInicioContrato': 'Date',
  'FechaDeFinContrato': 'Date',
  'DiasAdicionados': 'Int64',
  'FechaInicioLiquidacion': 'Date',
  'FechaFinLiquidacion': 'Date',
  'NombreEntidad': 'String',
  'NitEntidad': 'Int64',
  'EntidadCentralizada': 'String',
  'CodigoProveedor': 'Int64',
  'DocumentoProveedor': 'Int64',
  'ProveedorAdjudicado': 'String',
  'EsGrupo': 'String',
  'EsPyme': 'String',
  'NacionalidadRepresentanteLegal': 'String',
  'DomicilioRepresentanteLegal': 'Stri